In [36]:
import instructor
from pydantic import BaseModel
from openai import OpenAI

import dotenv
from tqdm.auto import trange

import json

In [20]:
dotenv.load_dotenv()

True

In [30]:
def get_initial_messages(transcript: str):
    return [
        {
            "role": "system",
            "content": [
                {
                    "type": "text",
                    "text": "You are a trivia bot writing fun questions for a trivia game. You have been given a transcript of a video. You need to write two questions based on the transcript. Do not refer explicitly to the transcript - it should be a valid question at a trivia night, for fans of the show, which is Hot Ones, Season 19. The questions should be in a JSON format."
                }
            ]
        },
        {
            "role": "user",
            "content": [
                {
                    "type": "text",
                    "text": f"Transcript: {transcript}"
                }
            ]
        }
    ]

In [31]:
class TriviaQuestions(BaseModel):
    question1: str
    answer1: str
    question2: str
    answer2: str


In [32]:

# Patch the OpenAI client
client = instructor.from_openai(OpenAI())

In [33]:
all_trivia = []
for i in trange(17):
    with open(f"transcripts/{i}.vtt") as f:
        text = f.read()
    msg = get_initial_messages(text)
    
    trivia = client.chat.completions.create(
        model="gpt-4o",
        response_model=TriviaQuestions,
        messages=msg,
    )
    
    all_trivia.append(trivia)

  0%|          | 0/17 [00:00<?, ?it/s]

In [34]:
all_questions = sum([[t.question1, t.question2] for t in all_trivia], [])
all_answers = sum([[t.answer1, t.answer2] for t in all_trivia], [])

In [37]:
all_questions

["Which magician's documentary adventure series titled 'Beyond Belief' is coming soon to Disney Plus?",
 'In Hot Ones Season 19, which magician recounted learning to expel water like a stream from a performer in Liberia?',
 'Who was the guest on the Hot Ones episode hosted by Sean Evans in which they joked about feeling their whiskers tingling?',
 'In the Hot Ones episode with Puss in Boots, what common beverage was mentioned multiple times as being essential during the challenge?',
 'Which charity is partnered with Hot Ones during their holiday fundraising efforts?',
 'Who won the Hot Ones 2022 Lifetime Achievement Award?',
 "Who did Emma Chamberlain claim she would marry, according to her 'F, Marry, Kill' choices involving milk types?",
 "What was Emma Chamberlain's major cooking success as mentioned on Hot Ones?",
 'Who hosted the Hot Ones season 19 Thanksgiving special with Israel Adesanya?',
 'Which UFC fighter mentioned in the Hot Ones season 19 Thanksgiving special has defended 

In [38]:
with open("questions.json", "w") as f:
    json.dump(all_questions, f)